In [ ]:
import numpy as np
import scipy as sp
import matplotlib.pyplot as plt
import math
print(f"numpy version: {np.__version__}")
print(f"scipy version: {sp.__version__}")
print(f"matplotlib version: {plt.matplotlib.__version__}")

In [ ]:
# estimating population parameters using random samples

n = 1000
y = np.random.normal(loc=100, scale=15, size=n)
print(f"sample = {y[0:10].round(2)}")
print(f"sample mean = {y.mean():.2f}")
print(f"sample sd =  {y.std():.2f}")

# standard error of the mean (SEM)
# SEM is the standard deviation of the theoretical distribution of the sample means
# (otherwise known as the "sampling distribution of means")

sem = y.std() / math.sqrt(n)
print(f"standard error of the mean = {sem:.2f}")

In [ ]:
# illustration of the role of sample size

samp_sizes = [10, 50, 100, 1000]
nsims = 10000
for n in samp_sizes:
    ymeans = np.zeros(nsims)
    for i in range(nsims):
        y = np.random.normal(0, 1, n)
        ymeans[i] = np.mean(y)
    plt.hist(ymeans, bins=50)
plt.xlim = (-1.1, 1.1)
plt.legend(samp_sizes)
plt.title("n=10, n=50, n=100, n=1000")
plt.xlabel("Sample mean")
plt.ylabel("Frequency")
plt.tight_layout()

In [ ]:
# correlations under the null hypothesis

n = 5
x = np.random.normal(0, 1, n)
y = np.random.normal(0, 1, n)
r = sp.stats.pearsonr(x, y)[0]
print(f"Correlation between x and y: {r}")
plt.figure(figsize=(5,4))
plt.scatter(x, y)
plt.xlabel("x")
plt.ylabel("y")
plt.title(f"Correlation between x and y: r={r.round(2)}, n={n}")

In [ ]:
# correlations & sample size

samp_sizes = [5, 10, 50, 100, 1000]
nsims = 10000
for n in samp_sizes:
    rvalues = np.zeros(nsims)
    for i in range(nsims):
        y1 = np.random.normal(0, 1, n)
        y2 = np.random.normal(0, 1, n)
        rvalues[i] = sp.stats.pearsonr(y1, y2)[0]
    plt.hist(rvalues, bins=50)
plt.xlim = (-1.1, 1.1)
plt.legend(samp_sizes)
plt.title("n=5, n=10, n=50, n=100, n=1000")
plt.xlabel("Pearson Correlation Coefficient r")
plt.ylabel("Frequency")
plt.tight_layout()

In [ ]:
# null hypothesis significance testing
# H0 true

pop_mean   = 100
pop_sd     = 15
pop_effect =  0
n          = 10
placebo = (np.random.randn(n) * pop_sd) + pop_mean
drug    = (np.random.randn(n) * pop_sd) + pop_mean + pop_effect
placebo, drug = placebo.round(decimals=0), drug.round(decimals=0)
print(f"placebo : {placebo}")
print(f"drug    : {drug}")
print(f"placebo mean : {placebo.mean()}")
print(f"drug mean    : {drug.mean()}")
results = sp.stats.ttest_ind(drug, placebo) # independent samples t-test
print(f"t({results.df}) = {results.statistic.round(2)}, p = {results.pvalue.round(5)}")

In [ ]:
# null hypothesis significance testing
# H0 false

pop_mean   = 100
pop_sd     = 15
pop_effect = 12
n          = 10
placebo = (np.random.randn(n) * pop_sd) + pop_mean
drug    = (np.random.randn(n) * 25) + pop_mean + pop_effect
placebo, drug = placebo.round(decimals=0), drug.round(decimals=0)
print(f"placebo : {placebo}")
print(f"drug    : {drug}")
print(f"placebo mean : {placebo.mean()}")
print(f"drug mean    : {drug.mean()}")
results = sp.stats.ttest_ind(drug, placebo) # independent samples t-test
print(f"t({results.df}) = {results.statistic.round(2)}, p = {results.pvalue.round(5)}")

In [ ]:
# function to simulate one experiment
def simulate_experiment(n=10, pop_effect=0, alpha=0.05, pop_mean=100, pop_sd=15, verbose=False):
    placebo = (np.random.randn(n) * pop_sd) + pop_mean
    drug    = (np.random.randn(n) * pop_sd) + pop_mean + pop_effect
    placebo, drug = placebo.round(decimals=0), drug.round(decimals=0)
    results = sp.stats.ttest_ind(drug, placebo) # independent samples t-test
    if (results.pvalue < alpha):
        results.decision = "H1"
    else:
        results.decision = "H0"
    if (verbose==True):
        print(f"placebo : {placebo}")
        print(f"drug    : {drug}")
        print(f"placebo mean : {placebo.mean()}")
        print(f"drug mean    : {drug.mean()}")
        print(f"t({results.df}) = {results.statistic.round(2)}, p = {results.pvalue.round(5)}")
    return results

In [ ]:
simulate_experiment(pop_effect = 100, verbose=True)

In [ ]:
# simulate many experiments under the null hypothesis

mean_diff =  0
n         = 10
pop_sd    = 15
alpha     = 0.01

n_simulations = 10000
p_values = np.zeros(n_simulations)
decision = np.zeros(n_simulations) # 0=H0, 1=H1
for i in range(n_simulations):
    results = simulate_experiment(n=n, alpha=alpha, pop_sd=pop_sd, pop_effect=mean_diff, verbose=False)
    p_values[i] = results.pvalue
    decision[i] = results.decision=="H1"
plt.hist(p_values, bins=20)
plt.xlim = (0,1)
plt.title("p-values under H0=true")
plt.xlabel("p-value")
plt.ylabel("Frequency")
plt.axvline(alpha, color="red")
plt.tight_layout()

type_I_errors = sum(decision)/n_simulations
print(f"you made a type I error {type_I_errors*100:.1f} % of the time ")

In [ ]:
# simulate many experiments under the alternate hypothesis

mean_diff = 15
n         = 18
pop_sd    = 13
alpha     = 0.01

n_simulations = 10000
p_values = np.zeros(n_simulations)
decision = np.zeros(n_simulations) # 0=H0, 1=H1
for i in range(n_simulations):
    results = simulate_experiment(n=n, alpha=alpha, pop_sd=pop_sd, pop_effect=mean_diff, verbose=False)
    p_values[i] = results.pvalue
    decision[i] = results.decision=="H1"
plt.hist(p_values, bins=50)
plt.xlim = (0,1)
plt.title("p-values under H0=true")
plt.xlabel("p-value")
plt.ylabel("Frequency")
plt.axvline(alpha, color="red")
plt.tight_layout()

type_II_errors = sum(decision==0)/n_simulations
print(f"you made a type II error {type_II_errors*100:.1f} % of the time ")
print(f"your statistical power was {1-type_II_errors:.1f}")